In [1]:
from __future__ import (absolute_import, division,
                        print_function, unicode_literals)
import numpy as np
import pickle
import cloudpickle
import json
import glob
import os

import matplotlib.pyplot as plt
%matplotlib inline

from enterprise.signals import signal_base
from enterprise.signals import gp_signals
from enterprise.pulsar import Pulsar
from enterprise.signals import parameter
from enterprise.signals import gp_priors

from enterprise_extensions import model_utils, blocks
from enterprise_extensions import model_orfs
from enterprise_extensions.frequentist import optimal_statistic as opt_stat
from enterprise.signals import selections

import h5py
import la_forge.core as co

import multiprocessing as mp

In [2]:
with open('/Users/kalistaw/Desktop/OS_2023_data/ng_models_tspan_ppta_fx_gamma_one_curn_none.pkl','rb') as fin:
    ng_pta_fx_gamma_curn = cloudpickle.load(fin)

In [3]:
with open('/Users/kalistaw/Desktop/OS_2023_data/epta_models_tspan_ppta_fx_gamma_one_curn_none.pkl','rb') as fin:
    epta_pta_fx_gamma_curn = cloudpickle.load(fin)

In [4]:
with open('/Users/kalistaw/Desktop/OS_2023_data/ppta_models_tspan_ppta_fx_gamma_one_curn_none.pkl','rb') as fin:
    ppta_pta_fx_gamma_curn = cloudpickle.load(fin)

In [5]:
with open('/Users/kalistaw/Desktop/OS_2023_data/ng_models_tspan_ppta_fx_gamma_one_curn_hd.pkl','rb') as fin:
    ng_pta_fx_gamma_hd = cloudpickle.load(fin)

In [6]:
with open('/Users/kalistaw/Desktop/OS_2023_data/epta_models_tspan_ppta_fx_gamma_one_curn_hd.pkl','rb') as fin:
    epta_pta_fx_gamma_hd = cloudpickle.load(fin)

In [7]:
with open('/Users/kalistaw/Desktop/OS_2023_data/ppta_models_tspan_ppta_fx_gamma_one_curn_hd.pkl','rb') as fin:
    ppta_pta_fx_gamma_hd = cloudpickle.load(fin)

In [12]:
with open('/Users/kalistaw/Desktop/OS_2023_data/ng_chain_fx_gamma_bf.pkl', 'r') as file:
      ng_samples_fx_gamma = json.load(file)

In [13]:
with open('/Users/kalistaw/Desktop/OS_2023_data/epta_chain_fx_gamma_bf.pkl', 'r') as file:
      epta_samples_fx_gamma = json.load(file)

In [14]:
with open('/Users/kalistaw/Desktop/OS_2023_data/ppta_chain_fx_gamma_bf.pkl', 'r') as file:
      ppta_samples_fx_gamma = json.load(file)

In [11]:
# with open('/Users/kalistaw/Desktop/OS_2023_data/three_models_tspan_ppta_fx_gamma_one_curn_orf_dipole.pkl','rb') as fin:
#     pta_fx_gamma_dipole = cloudpickle.load(fin)

In [17]:
# with open('/Users/kalistaw/Desktop/OS_2023_data/three_models_tspan_ppta_fx_gamma_one_curn_orf_monopole.pkl','rb') as fin:
#     pta_fx_gamma_mono = cloudpickle.load(fin)

In [2]:
def resampler(dict_array, pta, processes=1):
    if processes == 1:
        target_likelihoods = np.array([])
        for i in range(len(dict_array)):
            target_likelihoods = np.append(
                target_likelihoods,
                #pta.get_lnlikelihood({key:core_samples[key][i] for key in core_samples.keys()})
                pta.get_lnlikelihood(dict_array[i])
            )
    elif processes > 1:
        # FIXME : doesn't currently work. not sure if needed? 
        # i think numpy will just parallelize this?
        def likelihood_wrapper(*args):
            return pta.get_lnlikelihood([arg for arg in args])
        # uses the multiprocess module which is based off of multiprocessing but has some bug fix
        # sets up pool with number of processes
        pool = mp.Pool(processes=processes)
        # each column is passed to likelihood_wrapper, which
        for i in range(len(dict_array)):
            target_likelihoods = np.array(pool.starmap(likelihood_wrapper, pta.get_lnlikelihood(dict_array[i])))
    
    return target_likelihoods

#PTA_CRUN Approx
#PTA_HD Target 

def resampler_statistics(target_likelihoods, approx_likelihoods):
    resampler_stats = {}
    likelihoods = {'target_likelihoods': target_likelihoods, 'approx_likelihoods': approx_likelihoods}
    # calculate the ln_likelihood ratios.
    likelihoods['ln_likelihood_ratios'] = target_likelihoods - approx_likelihoods
    # the bayes factor is the average of the "weights"
    resampler_stats['bayes_factor'] = sum(np.exp(likelihoods['ln_likelihood_ratios'])) / len(likelihoods['ln_likelihood_ratios'])
    print("Bayes factor:  ", resampler_stats['bayes_factor'])
    resampler_stats['Ns'] = len(likelihoods['ln_likelihood_ratios'])
    resampler_stats['sigma_w'] = stdev(np.exp(likelihoods['ln_likelihood_ratios']))
    resampler_stats['n_eff'] = resampler_stats['Ns'] / ( 1. + ( resampler_stats['sigma_w'] / resampler_stats['bayes_factor'] ) ** 2)
    resampler_stats['efficiency'] = resampler_stats['n_eff'] / resampler_stats['Ns']
    resampler_stats['sigma_bf'] = resampler_stats['sigma_w'] / ( resampler_stats['efficiency'] * resampler_stats['Ns'] ) ** ( 1. / 2. )
    
    return resampler_stats, likelihoods

In [25]:
epta_approx_likelihoods_fx_gamma=resampler(epta_samples_fx_gamma,epta_pta_fx_gamma_curn)

In [26]:
epta_approx_likelihoods_fx_gamma

array([536599.95486076, 536602.72181613, 536598.99677703, 536586.26982443,
       536595.1250341 , 536597.77590771, 536601.83540498, 536600.06410085,
       536585.75016429, 536595.30530508, 536607.77229734, 536596.86108884,
       536603.75644002, 536590.38038182, 536598.08633842, 536604.48915784,
       536604.10050924, 536596.59208206, 536599.70589559, 536615.39190069,
       536595.32045271, 536576.56098258, 536585.02931814, 536601.7232407 ,
       536609.43151263, 536611.48917772, 536590.14211284, 536600.09447645,
       536596.42904231, 536602.78586793, 536603.65795436, 536586.41716667,
       536605.49099704, 536609.77241892, 536601.59947715, 536591.38683785,
       536605.9714784 , 536590.11289861, 536606.60975903, 536578.53019092,
       536591.35527095, 536600.8054008 , 536604.71166466, 536591.85685139,
       536597.67443977, 536594.09651085, 536573.38320388, 536582.91557092,
       536600.72871007, 536589.33238695, 536594.32481602, 536594.85213965,
       536603.35790981, 5

In [27]:
ppta_approx_likelihoods_fx_gamma=resampler(ppta_samples_fx_gamma,ppta_pta_fx_gamma_curn)

In [28]:
ppta_approx_likelihoods_fx_gamma

array([1440393.04593233, 1440388.11497957, 1440370.2963022 ,
       1440396.54058852, 1440383.5613362 , 1440379.6387091 ,
       1440378.20266379, 1440391.78295608, 1440382.75728875,
       1440398.81781694, 1440375.31816698, 1440392.1336761 ,
       1440384.03349123, 1440384.17919161, 1440393.50979208,
       1440374.55483523, 1440384.69084629, 1440392.66161373,
       1440395.01602938, 1440382.10470964, 1440373.72311724,
       1440356.18364276, 1440394.89445662, 1440389.31563743,
       1440390.38442819, 1440396.99615964, 1440372.66432881,
       1440390.48165341, 1440392.08571796, 1440368.07432636,
       1440371.57933368, 1440397.65717005, 1440373.94489567,
       1440390.29587528, 1440397.52037956, 1440393.42777786,
       1440389.5366002 , 1440381.77907961, 1440375.93552286,
       1440380.98671648, 1440384.7890167 , 1440402.36890692,
       1440384.63345092, 1440374.86570765, 1440406.2771475 ,
       1440395.85098826, 1440385.85972824, 1440393.77434535,
       1440376.90321249,

In [33]:
ng_approx_likelihoods_fx_gamma=resampler(ng_samples_fx_gamma,ng_pta_fx_gamma_curn)

In [34]:
ng_approx_likelihoods_fx_gamma

array([8411120.33747217, 8411138.04465519, 8411147.26172312,
       8411126.89792729, 8411139.97415964, 8411121.89580154,
       8411152.14755456, 8411143.29879741, 8411114.92936271,
       8411131.24336026, 8411148.34063046, 8411147.32531057,
       8411128.79559246, 8411126.10982708, 8411130.8247086 ,
       8411111.79827957, 8411150.51102815, 8411125.10538277,
       8411139.42590268, 8411141.63321169, 8411153.14937261,
       8411134.38016227, 8411143.24491142, 8411154.38691052,
       8411142.08180117, 8411143.95651382, 8411137.75239323,
       8411109.93687831, 8411120.79474238, 8411142.6582416 ,
       8411129.66984543, 8411128.88128034, 8411122.24074779,
       8411155.83215625, 8411135.94887421, 8411136.26920126,
       8411119.82050599, 8411118.6978012 , 8411148.52499871,
       8411149.78706457, 8411131.55226231, 8411121.68691829,
       8411133.6042376 , 8411139.70579733, 8411117.9218287 ,
       8411132.39810214, 8411122.72294666, 8411153.17367543,
       8411137.07159377,

In [37]:
ng_target_likelihoods_fx_gamma_hd=resampler(ng_samples_fx_gamma,ng_pta_fx_gamma_hd)

In [38]:
ng_target_likelihoods_fx_gamma_hd

array([8411126.88230996, 8411143.31161995, 8411153.87358829,
       8411132.78508756, 8411145.67654904, 8411127.63634643,
       8411161.0115983 , 8411151.34320006, 8411119.33682073,
       8411136.44654342, 8411155.34851195, 8411154.63825664,
       8411134.74208231, 8411129.65880806, 8411132.21637125,
       8411116.11479931, 8411155.30233636, 8411130.34101676,
       8411146.70158897, 8411150.42059062, 8411160.78627602,
       8411139.692504  , 8411149.35762779, 8411159.4450991 ,
       8411145.26738923, 8411149.63267265, 8411141.83003873,
       8411114.46241316, 8411127.28745729, 8411148.07203857,
       8411136.19058262, 8411134.74359982, 8411127.14236752,
       8411162.4247238 , 8411141.86945553, 8411142.62636553,
       8411121.84628352, 8411126.10733587, 8411153.93251385,
       8411154.65933667, 8411139.21350016, 8411127.76283082,
       8411134.71625483, 8411147.33782767, 8411123.43769709,
       8411131.87452886, 8411129.50809277, 8411157.20858925,
       8411142.7944702 ,

In [40]:
ppta_target_likelihoods_fx_gamma_hd=resampler(ppta_samples_fx_gamma,ppta_pta_fx_gamma_hd)

In [41]:
ppta_target_likelihoods_fx_gamma_hd

array([1440393.45906959, 1440389.01853865, 1440370.32060064,
       1440396.84569618, 1440384.40599635, 1440380.54667158,
       1440378.90446231, 1440392.0372967 , 1440382.50472707,
       1440399.88439177, 1440376.57365786, 1440392.6902356 ,
       1440384.50491017, 1440384.79980777, 1440394.53679156,
       1440374.62243333, 1440385.73019423, 1440393.74606955,
       1440394.70451342, 1440381.68157788, 1440373.48141177,
       1440356.31271763, 1440395.2921591 , 1440389.66121256,
       1440390.74221505, 1440397.66435751, 1440373.78244051,
       1440390.53809203, 1440392.77855527, 1440368.23412193,
       1440372.24467304, 1440398.24505652, 1440373.51755646,
       1440391.26914252, 1440397.31713913, 1440393.83771423,
       1440389.65792884, 1440381.58123276, 1440377.05334572,
       1440382.56654227, 1440385.32573955, 1440402.9624109 ,
       1440384.12655258, 1440375.27002832, 1440406.23353532,
       1440396.54131831, 1440385.7774668 , 1440394.32534203,
       1440377.68936259,

In [ ]:
epta_target_likelihoods_fx_gamma_hd=resampler(epta_samples_fx_gamma,epta_pta_fx_gamma_hd)

In [61]:
epta_target_likelihoods_fx_gamma_hd

array([536603.83624789, 536606.47138761, 536599.21065714, 536589.26340962,
       536596.84329714, 536599.68612282, 536602.97648033, 536602.74290266,
       536588.16739571, 536593.76424746, 536608.46999162, 536600.24998983,
       536607.85490868, 536593.87652615, 536602.35419218, 536605.71746101,
       536606.78947697, 536597.84368462, 536602.54454489, 536619.10607091,
       536597.91608134, 536577.91168136, 536586.29064283, 536604.95950186,
       536613.46797757, 536614.01595924, 536592.73669248, 536605.65014173,
       536600.92174157, 536606.24580116, 536606.64986259, 536587.52047422,
       536608.0545133 , 536612.54121815, 536605.02536261, 536594.72193111,
       536608.75152106, 536592.88507732, 536609.53026125, 536579.94311572,
       536594.6206869 , 536604.9648814 , 536609.15072333, 536595.15822641,
       536599.46459851, 536597.29089601, 536575.11644555, 536583.20258575,
       536604.03108178, 536591.8266071 , 536598.3855862 , 536598.55254353,
       536606.72218401, 5

In [43]:
from statistics import stdev

In [44]:
epta_resampler_stats_fx_gamma_hd, epta_likelihoods_fx_gamma_hd = resampler_statistics(epta_target_likelihoods_fx_gamma_hd,epta_approx_likelihoods_fx_gamma)

Bayes factor:   30.379144975749107


In [45]:
epta_resampler_stats_fx_gamma_hd

{'bayes_factor': 30.379144975749107,
 'Ns': 1000,
 'sigma_w': 55.15847027159317,
 'n_eff': 232.73925736688625,
 'efficiency': 0.23273925736688625,
 'sigma_bf': 3.6155751359925627}

In [46]:
ppta_resampler_stats_fx_gamma_hd, ppta_likelihoods_fx_gamma_hd = resampler_statistics(ppta_target_likelihoods_fx_gamma_hd,ppta_approx_likelihoods_fx_gamma)

Bayes factor:   1.8879302192324987


In [47]:
ppta_resampler_stats_fx_gamma_hd

{'bayes_factor': 1.8879302192324987,
 'Ns': 1000,
 'sigma_w': 0.982134230821804,
 'n_eff': 787.0135289293265,
 'efficiency': 0.7870135289293265,
 'sigma_bf': 0.03500900348683034}

In [49]:
ng_resampler_stats_fx_gamma_hd, ng_likelihoods_fx_gamma_hd = resampler_statistics(ng_target_likelihoods_fx_gamma_hd,ng_approx_likelihoods_fx_gamma)

Bayes factor:   993.5627443903553


In [50]:
ng_resampler_stats_fx_gamma_hd

{'bayes_factor': 993.5627443903553,
 'Ns': 1000,
 'sigma_w': 1941.2033710214544,
 'n_eff': 207.58698572802862,
 'efficiency': 0.2075869857280286,
 'sigma_bf': 134.73206788557653}

In [51]:
with open('/Users/kalistaw/Desktop/OS_2023_data/three_models_tspan_ppta_fx_gamma_one_curn_orf_none_elif.pkl','rb') as fin:
    comb_pta_fx_gamma_curn = cloudpickle.load(fin)

In [3]:
with open('/Users/kalistaw/Desktop/OS_2023_data/three_models_tspan_ppta_fx_gamma_one_curn_orf_spline_elif.pkl','rb') as fin:
    comb_pta_fx_gamma_spline = cloudpickle.load(fin)

In [52]:
with open('/Users/kalistaw/Desktop/OS_2023_data/three_models_tspan_ppta_fx_gamma_one_curn_orf_hd_elif.pkl','rb') as fin:
    comb_pta_fx_gamma_hd = cloudpickle.load(fin)

In [4]:
with open('/Users/kalistaw/Desktop/OS_2023_data/combined_three_pta_chain_fx_gamma_bf.pkl', 'r') as file:
      comb_samples_fx_gamma = json.load(file)

In [62]:
comb_approx_likelihoods_fx_gamma=resampler(comb_samples_fx_gamma,comb_pta_fx_gamma_curn)

In [63]:
comb_approx_likelihoods_fx_gamma

array([10388113.33822858, 10388128.88177507, 10388116.55444529,
       10388109.70793545, 10388118.66075467, 10388099.31019654,
       10388132.1855061 , 10388135.14585464, 10388083.43670866,
       10388125.36676942, 10388131.43097824, 10388136.32015482,
       10388116.58551325, 10388100.66940926, 10388122.42066515,
       10388090.84239911, 10388139.30250176, 10388114.35898494,
       10388134.14804203, 10388139.12981597, 10388122.19278309,
       10388067.12480555, 10388123.16855189, 10388145.42566749,
       10388141.89772774, 10388152.44140059, 10388100.55902853,
       10388100.51340954, 10388109.3094734 , 10388113.5184203 ,
       10388104.90708086, 10388112.95543839, 10388101.67655872,
       10388155.90044969, 10388135.06850179, 10388121.08378408,
       10388115.32831795, 10388090.5897724 , 10388131.070062  ,
       10388109.30412345, 10388107.6965792 , 10388124.86157137,
       10388122.94924952, 10388106.42839044, 10388121.87331524,
       10388122.34513841, 10388081.97535

In [64]:
comb_target_likelihoods_fx_gamma_hd=resampler(comb_samples_fx_gamma,comb_pta_fx_gamma_hd)

In [ ]:
np.seterror?--look for a traceback

In [65]:
comb_target_likelihoods_fx_gamma_hd

array([             -inf, 10388130.89718962,              -inf,
                    -inf,              -inf, 10388098.93972263,
                    -inf, 10388128.57757422,              -inf,
                    -inf,              -inf,              -inf,
                    -inf,              -inf,              -inf,
                    -inf,              -inf, 10388098.06105001,
                    -inf,              -inf,              -inf,
                    -inf, 10388127.05619793,              -inf,
       10388140.57429096, 10388171.6975662 ,              -inf,
                    -inf,              -inf, 10388106.66630623,
                    -inf, 10388121.89767538, 10388118.22495475,
                    -inf,              -inf,              -inf,
                    -inf,              -inf,              -inf,
                    -inf,              -inf,              -inf,
                    -inf,              -inf,              -inf,
                    -inf,              -

In [5]:
comb_target_likelihoods_fx_gamma_spline=resampler(comb_samples_fx_gamma,comb_pta_fx_gamma_spline)

TypeError: spline_orf() missing 1 required positional argument: 'params'

In [ ]:
TNR TNT rNr prior

In [88]:
TNR_0=comb_pta_fx_gamma_hd.get_TNr(comb_samples_fx_gamma[0])

In [120]:
for i in TNR_0: 
    boolarray=np.isinf(i) # True wherever pos-inf or neg-inf
    if True in boolarray: 
        print(np.where(np.isinf(i)))

for i in TNR_0: 
    boolarray=np.isnan(i) # True wherever nan
    if True in boolarray: 
        print(np.where(np.isnan(i)))

for i in TNR_0: 
    print(np.where(i==0))

(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], d

In [118]:
for i in TNR_0: 
    print(np.where(np.isinf(i))) # True wherever pos-inf or neg-inf

(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], d

In [110]:
TNT_0=comb_pta_fx_gamma_hd.get_TNT(comb_samples_fx_gamma[0])

In [121]:
for i in TNT_0: 
    boolarray=np.isinf(i) # True wherever pos-inf or neg-inf
    if True in boolarray: 
        print(np.where(np.isinf(i)))

for i in TNT_0: 
    boolarray=np.isnan(i) # True wherever nan
    if True in boolarray: 
        print(np.where(np.isnan(i)))

for i in TNT_0: 
    print(np.where(i==0))

(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int64), array([], dtype=int64))
(array([], dtype=int

In [112]:
rNr_0=comb_pta_fx_gamma_hd.get_rNr_logdet(comb_samples_fx_gamma[0])

In [122]:
for i in rNr_0: 
    boolarray=np.isinf(i) # True wherever pos-inf or neg-inf
    if True in boolarray: 
        print(np.where(np.isinf(i)))

for i in rNr_0: 
    boolarray=np.isnan(i) # True wherever nan
    if True in boolarray: 
        print(np.where(np.isnan(i)))

for i in rNr_0: 
    print(np.where(i==0))

(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], d

In [80]:
comb_pta_fx_gamma_hd.get_logsignalprior(comb_samples_fx_gamma[0])

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0]

In [86]:
comb_pta_fx_gamma_hd.get_logsignalprior(comb_samples_fx_gamma[1])

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0]

In [81]:
comb_pta_fx_gamma_hd.get_lnprior(comb_samples_fx_gamma[0])

/Users/anaconda3/envs/nanogw2/lib/python3.9/site-packages/enterprise/signals/parameter.py:62: RuntimeWarning: divide by zero encountered in log


-inf

In [82]:
comb_pta_fx_gamma_hd.get_lnlikelihood(comb_samples_fx_gamma[0])

-inf

In [123]:
comb_pta_fx_gamma_hd.get_lnlikelihood(comb_samples_fx_gamma[1])

10388130.897189617

In [126]:
resid_0=comb_pta_fx_gamma_hd.get_residuals()

In [130]:
for i in resid_0: 
    boolarray=np.isinf(i) # True wherever pos-inf or neg-inf
    if True in boolarray: 
        print(np.where(np.isinf(i)))

for i in resid_0: 
    boolarray=np.isnan(i) # True wherever nan
    if True in boolarray: 
        print(np.where(np.isnan(i)))

for i in resid_0: 
    print(np.where(i==0))

(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], dtype=int64),)
(array([], d

In [131]:
ndiag_0=comb_pta_fx_gamma_hd.get_ndiag(comb_samples_fx_gamma[0])

In [133]:
ndiag_0

[ndarray_alt([4.67280139e-11, 6.44732214e-11, 1.65071378e-11,
              5.24312236e-11, 4.20813329e-11, 2.05161545e-11,
              2.01795813e-11, 1.62994565e-11, 2.89697232e-11,
              1.65309784e-11, 2.25533562e-11, 6.17907849e-11,
              4.61656619e-11, 3.56746269e-11, 8.46491118e-11,
              5.85237414e-11, 4.42120711e-11, 4.68495930e-11,
              6.42146308e-12, 5.81773873e-12, 6.41578877e-12,
              6.19087489e-12, 1.13855013e-11, 7.00985371e-12,
              9.07505403e-12, 8.85900943e-12, 6.39883988e-12,
              7.87453050e-12, 1.69632171e-11, 1.37895737e-11,
              2.27708738e-11, 3.50453106e-11, 3.30383216e-11,
              1.31823866e-11, 8.22743529e-11, 1.79034439e-11,
              2.30406335e-11, 2.21873932e-11, 1.61540694e-11,
              2.29322448e-11, 3.49291779e-11, 3.22839104e-11,
              1.75777233e-11, 2.40973688e-11, 9.45078070e-12,
              4.27190169e-12, 1.14155512e-11, 2.31764272e-12,
        

In [132]:
for i in ndiag_0: 
    boolarray=np.isinf(i) # True wherever pos-inf or neg-inf
    if True in boolarray: 
        print(np.where(np.isinf(i)))

for i in ndiag_0: 
    boolarray=np.isnan(i) # True wherever nan
    if True in boolarray: 
        print(np.where(np.isnan(i)))

for i in ndiag_0: 
    print(np.where(i==0))

TypeError: ufunc 'isinf' not supported for the input types, and the inputs could not be safely coerced to any supported types according to the casting rule ''safe''

In [134]:
comb_pta_fx_gamma_hd.get_delay(comb_samples_fx_gamma[0])

[0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 array([ 0.00000000e+00,  0.00000000e+00,  0.00000000e+00, ...,
        -1.06357514e-25, -1.25809655e-25, -1.47317253e-25]),
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 array([2.41442656e-07, 2.33293283e-07, 2.38679387e-07, ...,
        3.69828518e-08, 3.96163132e-08, 3.73925211e-08]),
 array([7.18466980e-08, 7.22662398e-08, 7.10185009e-08, ...,
        2.24666546e-08, 2.09097078e-08, 2.09990118e-08]),
 array([2.33625823e-08, 2.34413768e-08, 2.43350758e-08, ...,
        6.32898372e-07, 6.28422285e-07, 6.23990695e-07]),
 array([8.18538019e-07, 8.03309737e-07, 7.88502502e-07, ...,
        4.73137184e-08, 4.86678046e-08, 4.79633104e-08]),
 array([1.39362899e-06, 1.34249103e-06, 1.36770158e-06, ...,
        4.57729067e-08, 4.38057435e-08, 4.72154819e-08]),
 array([1.21299234e-07, 1.19189087e-07, 1.14382465e-07, ...,
        3.77649667e-07, 3.79678365e-07, 3.75077001e-07]),
 array([8.96915244e-08, 8.83626549e-08, 8.68551942e-08, .

In [137]:
phiinv_0=comb_pta_fx_gamma_hd.get_phiinv(comb_samples_fx_gamma[0])

In [139]:
for i in phiinv_0: 
    boolarray=np.isinf(i) # True wherever pos-inf or neg-inf
    if True in boolarray: 
        print(np.where(np.isinf(i)))

for i in phiinv_0: 
    boolarray=np.isnan(i) # True wherever nan
    if True in boolarray: 
        print(np.where(np.isnan(i)))

In [140]:
for i in phiinv_0: 
    print(np.where(i==0))

(array([    1,     2,     3, ..., 34219, 34220, 34221]),)
(array([    0,     2,     3, ..., 34219, 34220, 34221]),)
(array([    0,     1,     3, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

...

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

In [153]:
phi_0=comb_pta_fx_gamma_hd.get_phi(comb_samples_fx_gamma[0])

In [154]:
for i in phi_0: 
    boolarray=np.isinf(i) # True wherever pos-inf or neg-inf
    if True in boolarray: 
        print(np.where(np.isinf(i)))

for i in phi_0: 
    boolarray=np.isnan(i) # True wherever nan
    if True in boolarray: 
        print(np.where(np.isnan(i)))

In [155]:
for i in phi_0: 
    print(np.where(i==0))

(array([    1,     2,     3, ..., 34219, 34220, 34221]),)
(array([    0,     2,     3, ..., 34219, 34220, 34221]),)
(array([    0,     1,     3, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

...

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,     1,     2, ..., 34219, 34220, 34221]),)
(array([    0,

In [ ]:
with open('/Users/kalistaw/Desktop/OS_2023_data/three_models_tspan_ppta_var_gamma.pkl','rb') as fin:
    pta_var_gamma_curn = cloudpickle.load(fin)

In [ ]:
with open('/Users/kalistaw/Desktop/OS_2023_data/three_models_tspan_ppta_var_gamma_orf_hd.pkl','rb') as fin:
    pta_var_gamma_hd = cloudpickle.load(fin)

In [ ]:
with open('/Users/kalistaw/Desktop/OS_2023_data/combined_three_pta_chain_var_gamma_dmgp_set.pkl', 'r') as file:
      samples_var_gamma_ = json.load(file)

In [ ]:
approx_likelihoods_var_gamma=resampler(samples_var_gamma_,pta_var_gamma_curn)

In [ ]:
target_likelihoods_var_gamma=resampler(samples_var_gamma_,pta_var_gamma_hd)

In [ ]:
resampler_stats_var_gamma, likelihoods_var_gamma = resampler_statistics(target_likelihoods_var_gamma,approx_likelihoods_var_gamma)

In [12]:
target_likelihoods_fx_gamma=resampler(samples_fx_gamma,pta_fx_gamma_dipole)

In [19]:
target_likelihoods_fx_gamma_mono=resampler(samples_fx_gamma,pta_fx_gamma_mono)

In [21]:
resampler_stats_fx_gamma_mono, likelihoods_fx_gamma_mono = resampler_statistics(target_likelihoods_fx_gamma_mono,approx_likelihoods_fx_gamma)

Bayes factor:   8.596215873813081e-77


In [22]:
resampler_stats_fx_gamma_mono

{'bayes_factor': 8.596215873813081e-77,
 'Ns': 1000,
 'sigma_w': 2.7183601463443434e-75,
 'n_eff': 0.9990024643296438,
 'efficiency': 0.0009990024643296439,
 'sigma_bf': 2.7197169921607735e-75}

In [ ]:
resampler_stats_fx_gamma, likelihoods_fx_gamma = resampler_statistics(target_likelihoods_fx_gamma,approx_likelihoods_fx_gamma)